In [18]:
import pandas as pd
from dadata import Dadata

### Loading the dataset

In [3]:
df = pd.read_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/dataset.csv')
df.info()

C:\ProgramData\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3166: DtypeWarning: Columns (13,14) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1653596 entries, 0 to 1653595
Data columns (total 15 columns):
 #   Column                  Non-Null Count    Dtype  
---  ------                  --------------    -----  
 0   user_id                 1653596 non-null  int64  
 1   user_ext                1653596 non-null  int64  
 2   age                     1653460 non-null  float64
 3   exp                     1652029 non-null  float64
 4   sex                     1653596 non-null  object 
 5   phone_code              1653506 non-null  float64
 6   license_category        1277528 non-null  object 
 7   birth_place             1320415 non-null  object 
 8   country                 1026162 non-null  object 
 9   region                  1026164 non-null  object 
 10  city                    1026164 non-null  object 
 11  passport_citizenship    1651817 non-null  object 
 12  PassportNumber          1651817 non-null  object 
 13  PassportDepartmentCode  632036 non-null   object 
 14  Pa

In [5]:
df.loc[10:20, :]

user_id  user_ext        age        exp sex  phone_code license_category  \
10  19500039       224  36.591376  17.771389   М       903.0      A,A1,B,B1,M   
11  19500048       270  26.568104   3.906913   М       925.0                В   
12  19500049       292  28.867899   9.426420   М       926.0               ВM   
13  19500053       303  31.679671  12.766598   М       926.0              В С   
14  19500064       412  29.749487  11.890486   М       964.0                в   
15  19500068       437  35.463381  17.136208   М       910.0         В, В1, М   
16  19500082       530  39.482546  20.531143   М       916.0                В   
17  19500084       545  28.175222  10.225873   М       915.0              А,В   
18  19500086       551  35.791923        NaN   М       962.0                в   
19  19500095       592  32.306639        NaN   М       965.0                В   
20  19500098       613  28.599589   5.812457   М       925.0                в   

                                  birth_place    country               region  \
10                                   Г С4ГГВГ        NaN                  NaN   
11                                ГОР. МОСКВА     Россия               Москва   
12                               ГОРОД МОСКВА     Россия               Москва   
13                              ГОР. АЛМА-АТА  Казахстан  Алматинская область   
14                               город Москва     Россия               Москва   
15                                ГОР. МОСКВА     Россия               Москва   
16                                  ГОР. ОРЕЛ     Россия    Орловская область   
17                                гор. Москва     Россия               Москва   
18                                гор. Курган     Россия   Курганская область   
19  с. Бешалма гор. Комрат республика Молдова        NaN                  NaN   
20                             гор. Хабаровск     Россия     Хабаровский край   

         city passport_citizenship  PassportNumber PassportDepartmentCode  \
10        NaN              Russian     4500 916251                772-082   
11     Москва              Russian     4510 187931                770-106   
12     Москва              Russian     4510 860356                770-032   
13     Алматы              Russian     4507 463220                772-085   
14     Москва              Russian     4508 563849                772-089   
15     Москва              Russian     4504 029170                772-073   
16       Орёл              Russian     4516 705179                770-080   
17     Москва              Russian     4510 298810                770-085   
18     Курган              Russian  3702 № 637821                 451-001   
19        NaN              Russian     2208 343199                520-014   
20  Хабаровск              Russian     2813 258785                690-036   

                                 PassportRegistration  
10        Г. МОСКВА, ТРЕХГОРНЫЙ ВАЛ, д.12, к.1, кв.13  
11     г. Москва, Новочеркасский бульв., д.36, кв.587  
12       г. Москва, ул. Дербеневская, д.14, к.3, кв.5  
13                 МОСКВА, ЯХРОМСКАЯ, д.9, к.1, кв.36  
14             г. Москва, ул. Коненкова, д. 9, кв. 17  
15        г. Москва, Открытое шоссе, д.19, к.3, кв.21  
16          ГОР.МОСКВА, УЛ.АБРАМЦЕВСКАЯ, д.12, кв.197  
17       г. Москва, ул. Декабристов, д.20, к.3, кв.12  
18  Курганская обл., г. Курган, ул. Савельева, д. ...  
19  Нижегородская область, г. Выкса, Мотмос мкр., ...  
20  Тверская область, г. Торжок, 1-ый пер. Металли...

### Loading additional data

In [8]:
# Birthplaces classification. Classified using personal experience
bp_classified = pd.read_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/data_lib/birthplaces_classified_lib.csv')
bp_country_classified = bp_classified[['bp_country', 'bp_country_group']]
bp_region_classified = bp_classified[['bp_region', 'bp_region_group_detailed']]
bp_region_classified = bp_region_classified.drop_duplicates(subset = 'bp_region')

### Merging data

In [9]:
df = pd.merge(df, bp_region_classified, left_on = 'region', right_on = 'bp_region', how = 'left')

### Enriching the dataset

In [11]:
df = df.drop(columns = ['user_ext', 'phone_code', 'license_category', 'PassportNumber', 'PassportDepartmentCode'])

### Finding unrecognized birth places

In [13]:
unrec_bp = df[['user_id', 'birth_place', 'country']]
unrec_bp = unrec_bp.loc[unrec_bp.country.isnull()]
unrec_bp = unrec_bp.loc[unrec_bp.birth_place.notnull()]
unrec_bp = unrec_bp[['user_id', 'birth_place']]
unrec_bp = unrec_bp.reset_index(drop = True)
unrec_bp.to_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/unrecognized_bp.csv', encoding = 'utf-8-sig', index = False)

In [28]:
unrec_bp = pd.read_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/unrecognized_bp.csv')

In [34]:
unrec_bp.birth_place[79726:]

79726        ПОС. ТАТАЛ ЮСТИНСКИЙ РАЙОН РЕСПУБЛИКА КАЛМЫКИЯ
79727                     С. ЧАЧАРАКИ ГОРОД АХАЛЦИХЕ ГРУЗИЯ
79728     С.Тулейкен КАРАСУЙСКОГО РАЙОНЕ ОШСКОЙ ОБЛ. КИР...
79729                     ГОР ПОДПОРОЖЬЕ ЛЕНИНГРАДСКОЙ ОБЛ 
79730                                   ГОР НИЖНИЙ НОВГОРОД
                                ...                        
294248    Е. ПОЛОВИННОЕ КРАСНОЗЕРСКОГО РАЙОНА НОВЕСМБРКО...
294249                   Г. ГУМИСТА СУХУМСКИЙ РАЙОН АБХАЗИЯ
294250       С. БОБРАВА РАКИТЯНСКОГО Р-НА БЕЛГОРОДСКОЙ ОБЛ.
294251         ПОС. БАРАНЧИНСКИЙ ГОР. К7ВЫ СВЕРДЛОВСКОЙ ОБЛ
294252                        ГОР. ИРКУТСК РАЙОНА ИРКУТСКОЙ
Name: birth_place, Length: 214527, dtype: object

### Concating recognized birthplaces

In [2]:
unrec_bp = pd.read_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/data_lib/unrecognized_bp.csv')
rec_bp1 = pd.read_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/data_lib/processed_bp_v2_part1.csv')
rec_bp2 = pd.read_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/data_lib/processed_bp_v2_part2.csv')

In [7]:
rec_bp = pd.concat([rec_bp1, rec_bp2], axis = 0, ignore_index = True)
rec_bp = rec_bp[['address']]
rec_bp

address
0                         ГОР. МАЙКОП РЕСПУБЛИКА АДЫГЕЯ 
1                               Г. ПУШКИНО МОСКОВСКОЙ ОА
2                          ГОР. ШШЧУРННСК ТАМБОВСКОЙ ОБЛ
3                          гор. Сусуман Магаданская обл.
4                 ГОР. НАЛЬЧИК КАБАРДИНО-БАЛКАРСКОЙ АЕСР
...                                                  ...
96567           ГОРОД ЖЕЛЕЗНОДОРОЖНЫЙ МОСКОВСКАЯ ОБЛАСТЬ
96568    С. СВЕРДЛОВО КАЛИНИНСКОГО Р-НА САРАТОВСКОЙ ОБЛ.
96569  УЧКЕКЕН МАЛОКАРАЧАЕВСКИЙ РАЙОН СТАВРОПОЛЬСКИЙ ...
96570                              ГОР. СУРГУТ ТЮМЕНСКАЯ
96571    ПОС. КРУТАЯ ГОРКА ОКТЯБРЬСКОГО Р-НА ОМСКОЙ ОБЛ.

[96572 rows x 1 columns]

In [10]:
test = pd.merge(unrec_bp, rec_bp, left_on = 'birth_place', right_on = 'address', how = 'left')
test = test.dropna()
test = test.drop_duplicates()
test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 375607 entries, 4 to 550963
Data columns (total 3 columns):
 #   Column       Non-Null Count   Dtype 
---  ------       --------------   ----- 
 0   user_id      375607 non-null  int64 
 1   birth_place  375607 non-null  object
 2   address      375607 non-null  object
dtypes: int64(1), object(2)
memory usage: 11.5+ MB


In [12]:
test.tail(n=25)

user_id                                        birth_place  \
550885  2094500967                  Г. БЕЛОВО КЕМЕРОВСКАЯ ОБЛ. РОССИЯ   
550886  2094500967                  Г. БЕЛОВО КЕМЕРОВСКАЯ ОБЛ. РОССИЯ   
550887  2094500967                  Г. БЕЛОВО КЕМЕРОВСКАЯ ОБЛ. РОССИЯ   
550891  2097000071         С. ИВАНОВКА ИВАНОВСКОГО Р-НА АМУРСКОЙ ОБЛ.   
550892  2097000071         С. ИВАНОВКА ИВАНОВСКОГО Р-НА АМУРСКОЙ ОБЛ.   
550893  2097000071         С. ИВАНОВКА ИВАНОВСКОГО Р-НА АМУРСКОЙ ОБЛ.   
550896  2097000230                                    ГОР. ПАРХИМ ГДР   
550897  2097000230                                    ГОР. ПАРХИМ ГДР   
550900  2097000319                                  Г. МАГАДАН РОССИЯ   
550901  2097000319                                  Г. МАГАДАН РОССИЯ   
550909  2097250011           С. ОЛЯ ЛИМАНСКОГО Р-НА АСТРАХАНСКОЙ ОБЛ.   
550910  2097250011           С. ОЛЯ ЛИМАНСКОГО Р-НА АСТРАХАНСКОЙ ОБЛ.   
550911  2097250011           С. ОЛЯ ЛИМАНСКОГО Р-НА АСТРАХАНСКОЙ ОБЛ.   
550918  2097250611                                              ОСКВА   
550922  2097250980  Г. МИРНЫЙ МИРНИНСКИЙ РАЙОН РЕСПУБЛИКА САХА (ЯК...   
550923  2097250980  Г. МИРНЫЙ МИРНИНСКИЙ РАЙОН РЕСПУБЛИКА САХА (ЯК...   
550938  2097500904                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ   
550939  2097500904                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ   
550940  2097500904                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ   
550941  2097500904                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ   
550942  2097500904                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ   
550958  2100000453                         Г. ПЫТАЛОВО ПСКОВСКАЯ ОБЛ.   
550961  2100000712             ГОР. КУРГАНИНСК КРАСНОДАРСКОГО КРАЯ РФ   
550962  2100000712             ГОР. КУРГАНИНСК КРАСНОДАРСКОГО КРАЯ РФ   
550963  2100000712             ГОР. КУРГАНИНСК КРАСНОДАРСКОГО КРАЯ РФ   

                                                  address  
550885                  Г. БЕЛОВО КЕМЕРОВСКАЯ ОБЛ. РОССИЯ  
550886                  Г. БЕЛОВО КЕМЕРОВСКАЯ ОБЛ. РОССИЯ  
550887                  Г. БЕЛОВО КЕМЕРОВСКАЯ ОБЛ. РОССИЯ  
550891         С. ИВАНОВКА ИВАНОВСКОГО Р-НА АМУРСКОЙ ОБЛ.  
550892         С. ИВАНОВКА ИВАНОВСКОГО Р-НА АМУРСКОЙ ОБЛ.  
550893         С. ИВАНОВКА ИВАНОВСКОГО Р-НА АМУРСКОЙ ОБЛ.  
550896                                    ГОР. ПАРХИМ ГДР  
550897                                    ГОР. ПАРХИМ ГДР  
550900                                  Г. МАГАДАН РОССИЯ  
550901                                  Г. МАГАДАН РОССИЯ  
550909           С. ОЛЯ ЛИМАНСКОГО Р-НА АСТРАХАНСКОЙ ОБЛ.  
550910           С. ОЛЯ ЛИМАНСКОГО Р-НА АСТРАХАНСКОЙ ОБЛ.  
550911           С. ОЛЯ ЛИМАНСКОГО Р-НА АСТРАХАНСКОЙ ОБЛ.  
550918                                              ОСКВА  
550922  Г. МИРНЫЙ МИРНИНСКИЙ РАЙОН РЕСПУБЛИКА САХА (ЯК...  
550923  Г. МИРНЫЙ МИРНИНСКИЙ РАЙОН РЕСПУБЛИКА САХА (ЯК...  
550938                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ  
550939                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ  
550940                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ  
550941                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ  
550942                    Г. БЕЛОЯРСКИЙ ТЮМЕНСКОЙ ОБЛАСТИ  
550958                         Г. ПЫТАЛОВО ПСКОВСКАЯ ОБЛ.  
550961             ГОР. КУРГАНИНСК КРАСНОДАРСКОГО КРАЯ РФ  
550962             ГОР. КУРГАНИНСК КРАСНОДАРСКОГО КРАЯ РФ  
550963             ГОР. КУРГАНИНСК КРАСНОДАРСКОГО КРАЯ РФ

### Passing unrecognized birthplaces through the DaData algorithm

In [20]:
unrec_bp = pd.read_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/data_lib/unrecognized_bp.csv')

token = '015dccf61fdf5335d60d2aafc5f96b26a031d078'
secret = '70c9d7a82db5ab5ec095b3f02983ee119b13a7eb'

dadata = Dadata(token, secret)

address_data = []

for address, user_id in zip(unrec_bp.birth_place[188526:], unrec_bp.user_id[188526:]):
    response = dadata.suggest("address", address)
    if len(response) == 0:
        output = response
    else:
        output = response[0]['data']
        output['user_id'] = user_id
        output['address'] = address
        address_data.append(output)
        print(str(len(address_data))+" addresses have been processed")

1 addresses have been processed
2 addresses have been processed
3 addresses have been processed
4 addresses have been processed
5 addresses have been processed
6 addresses have been processed
7 addresses have been processed
8 addresses have been processed
9 addresses have been processed
10 addresses have been processed
11 addresses have been processed
12 addresses have been processed
13 addresses have been processed
14 addresses have been processed
15 addresses have been processed
16 addresses have been processed
17 addresses have been processed
18 addresses have been processed
19 addresses have been processed
20 addresses have been processed
21 addresses have been processed
22 addresses have been processed
23 addresses have been processed
24 addresses have been processed
25 addresses have been processed
26 addresses have been processed
27 addresses have been processed
28 addresses have been processed
29 addresses have been processed
30 addresses have been processed
31 addresses have b

248 addresses have been processed
249 addresses have been processed
250 addresses have been processed
251 addresses have been processed
252 addresses have been processed
253 addresses have been processed
254 addresses have been processed
255 addresses have been processed
256 addresses have been processed
257 addresses have been processed
258 addresses have been processed
259 addresses have been processed
260 addresses have been processed
261 addresses have been processed
262 addresses have been processed
263 addresses have been processed
264 addresses have been processed
265 addresses have been processed
266 addresses have been processed
267 addresses have been processed
268 addresses have been processed
269 addresses have been processed
270 addresses have been processed
271 addresses have been processed
272 addresses have been processed
273 addresses have been processed
274 addresses have been processed
275 addresses have been processed
276 addresses have been processed
277 addresses 

490 addresses have been processed
491 addresses have been processed
492 addresses have been processed
493 addresses have been processed
494 addresses have been processed
495 addresses have been processed
496 addresses have been processed
497 addresses have been processed
498 addresses have been processed
499 addresses have been processed
500 addresses have been processed
501 addresses have been processed
502 addresses have been processed
503 addresses have been processed
504 addresses have been processed
505 addresses have been processed
506 addresses have been processed
507 addresses have been processed
508 addresses have been processed
509 addresses have been processed
510 addresses have been processed
511 addresses have been processed
512 addresses have been processed
513 addresses have been processed
514 addresses have been processed
515 addresses have been processed
516 addresses have been processed
517 addresses have been processed
518 addresses have been processed
519 addresses 

734 addresses have been processed
735 addresses have been processed
736 addresses have been processed
737 addresses have been processed
738 addresses have been processed
739 addresses have been processed
740 addresses have been processed
741 addresses have been processed
742 addresses have been processed
743 addresses have been processed
744 addresses have been processed
745 addresses have been processed
746 addresses have been processed
747 addresses have been processed
748 addresses have been processed
749 addresses have been processed
750 addresses have been processed
751 addresses have been processed
752 addresses have been processed
753 addresses have been processed
754 addresses have been processed
755 addresses have been processed
756 addresses have been processed
757 addresses have been processed
758 addresses have been processed
759 addresses have been processed
760 addresses have been processed
761 addresses have been processed
762 addresses have been processed
763 addresses 

978 addresses have been processed
979 addresses have been processed
980 addresses have been processed
981 addresses have been processed
982 addresses have been processed
983 addresses have been processed
984 addresses have been processed
985 addresses have been processed
986 addresses have been processed
987 addresses have been processed
988 addresses have been processed
989 addresses have been processed
990 addresses have been processed
991 addresses have been processed
992 addresses have been processed
993 addresses have been processed
994 addresses have been processed
995 addresses have been processed
996 addresses have been processed
997 addresses have been processed
998 addresses have been processed
999 addresses have been processed
1000 addresses have been processed
1001 addresses have been processed
1002 addresses have been processed
1003 addresses have been processed
1004 addresses have been processed
1005 addresses have been processed
1006 addresses have been processed
1007 ad

...

66596 addresses have been processed
66597 addresses have been processed
66598 addresses have been processed
66599 addresses have been processed
66600 addresses have been processed
66601 addresses have been processed
66602 addresses have been processed
66603 addresses have been processed
66604 addresses have been processed
66605 addresses have been processed
66606 addresses have been processed
66607 addresses have been processed
66608 addresses have been processed
66609 addresses have been processed
66610 addresses have been processed
66611 addresses have been processed
66612 addresses have been processed
66613 addresses have been processed
66614 addresses have been processed
66615 addresses have been processed
66616 addresses have been processed
66617 addresses have been processed
66618 addresses have been processed
66619 addresses have been processed
66620 addresses have been processed
66621 addresses have been processed
66622 addresses have been processed
66623 addresses have been pr

66824 addresses have been processed
66825 addresses have been processed
66826 addresses have been processed
66827 addresses have been processed
66828 addresses have been processed
66829 addresses have been processed
66830 addresses have been processed
66831 addresses have been processed
66832 addresses have been processed
66833 addresses have been processed
66834 addresses have been processed
66835 addresses have been processed
66836 addresses have been processed
66837 addresses have been processed
66838 addresses have been processed
66839 addresses have been processed
66840 addresses have been processed
66841 addresses have been processed
66842 addresses have been processed
66843 addresses have been processed
66844 addresses have been processed
66845 addresses have been processed
66846 addresses have been processed
66847 addresses have been processed
66848 addresses have been processed
66849 addresses have been processed
66850 addresses have been processed
66851 addresses have been pr

67054 addresses have been processed
67055 addresses have been processed
67056 addresses have been processed
67057 addresses have been processed
67058 addresses have been processed
67059 addresses have been processed
67060 addresses have been processed
67061 addresses have been processed
67062 addresses have been processed
67063 addresses have been processed
67064 addresses have been processed
67065 addresses have been processed
67066 addresses have been processed
67067 addresses have been processed
67068 addresses have been processed
67069 addresses have been processed
67070 addresses have been processed
67071 addresses have been processed
67072 addresses have been processed
67073 addresses have been processed
67074 addresses have been processed
67075 addresses have been processed
67076 addresses have been processed
67077 addresses have been processed
67078 addresses have been processed
67079 addresses have been processed
67080 addresses have been processed
67081 addresses have been pr

67285 addresses have been processed
67286 addresses have been processed
67287 addresses have been processed
67288 addresses have been processed
67289 addresses have been processed
67290 addresses have been processed
67291 addresses have been processed
67292 addresses have been processed
67293 addresses have been processed
67294 addresses have been processed
67295 addresses have been processed
67296 addresses have been processed
67297 addresses have been processed
67298 addresses have been processed
67299 addresses have been processed
67300 addresses have been processed
67301 addresses have been processed
67302 addresses have been processed
67303 addresses have been processed
67304 addresses have been processed
67305 addresses have been processed
67306 addresses have been processed
67307 addresses have been processed
67308 addresses have been processed
67309 addresses have been processed
67310 addresses have been processed
67311 addresses have been processed
67312 addresses have been pr

HTTPError: 403 Client Error: Forbidden for url: https://suggestions.dadata.ru/suggestions/api/4_1/rs/suggest/address

In [24]:
address_data

[{'postal_code': '385000',
  'country': 'Россия',
  'country_iso_code': 'RU',
  'federal_district': None,
  'region_fias_id': 'd8327a56-80de-4df2-815c-4f6ab1224c50',
  'region_kladr_id': '0100000000000',
  'region_iso_code': 'RU-AD',
  'region_with_type': 'Респ Адыгея',
  'region_type': 'Респ',
  'region_type_full': 'республика',
  'region': 'Адыгея',
  'area_fias_id': None,
  'area_kladr_id': None,
  'area_with_type': None,
  'area_type': None,
  'area_type_full': None,
  'area': None,
  'city_fias_id': '8cfbe842-e803-49ca-9347-1ef90481dd98',
  'city_kladr_id': '0100000100000',
  'city_with_type': 'г Майкоп',
  'city_type': 'г',
  'city_type_full': 'город',
  'city': 'Майкоп',
  'city_area': None,
  'city_district_fias_id': None,
  'city_district_kladr_id': None,
  'city_district_with_type': None,
  'city_district_type': None,
  'city_district_type_full': None,
  'city_district': None,
  'settlement_fias_id': None,
  'settlement_kladr_id': None,
  'settlement_with_type': None,
  'sett

### Selecting only required columns

In [21]:
columns = ['user_id', 'address', 'country','region_with_type', 'area_type_full', 'area', 'city_type_full', 'city', 'city_area',\
           'city_district_type_full', 'city_district', 'settlement_type_full', 'settlement']

In [22]:
empty_df = pd.DataFrame({})
adrs = empty_df.append(address_data, True)
adrs = adrs[columns]
adrs

user_id                                            address country  \
0        43003038  Рп Аксарайский Астраханской Обл Карсноярского ...  Россия   
1        43003063     ПОС. АРГЕЛ НАИРИЙСКИЙ РАЙОН РЕСПУБЛИКА АРМЕНИЯ  Россия   
2        43003135                                             Баксан  Россия   
3        43003153                     Красноярский Край, Г. Норильск  Россия   
4        43003220            ОРМИЛОВКА. КОРМИЛОВСКИЙ Р-Н ОМСКАЯ ОБЛ.  Россия   
...           ...                                                ...     ...   
67398  1960001013      ДЕР. ТИМКОВО БОЛОГОВСКОГО Р. ЧГ ТВЕРСКОЙ ОБЛ.  Россия   
67399  1960001021       ДЕР. БАТОВО ГАТЧИНСКОГО РАЙОНА ЛЕНИНГРАДСКОЙ  Россия   
67400  1960001078       ПОС. АЛЕКСЕЕВСК КИРЕНСКИЙ Р-Н ИРКУТСКАЯ ОБЛ.  Россия   
67401  1960001227                   ГОР. ФУРМАНОВ ИВАНОВСКОЙ ОБЛАСТИ  Россия   
67402  1960250126                     ГОР. ВЕЛИЖ ЛУКИ ПСКОВСКАЯ ОБЛ.  Россия   

                region_with_type area_type_full          area city_type_full  \
0               Астраханская обл          район  Красноярский           None   
1                 Ивановская обл          район       Шуйский          город   
2      Кабардино-Балкарская Респ          район    Баксанский           None   
3              Красноярский край           None          None          город   
4                     Омская обл          район  Кормиловский           None   
...                          ...            ...           ...            ...   
67398               Тверская обл          район   Бологовский           None   
67399          Ленинградская обл          район    Гатчинский           None   
67400              Иркутская обл          район     Киренский           None   
67401             Ивановская обл          район  Фурмановский          город   
67402              Псковская обл          район     Печорский           None   

           city city_area city_district_type_full city_district  \
0          None      None                    None          None   
1           Шуя      None                    None          None   
2          None      None                    None          None   
3      Норильск      None                    None          None   
4          None      None                    None          None   
...         ...       ...                     ...           ...   
67398      None      None                    None          None   
67399      None      None                    None          None   
67400      None      None                    None          None   
67401  Фурманов      None                    None          None   
67402      None      None                    None          None   

      settlement_type_full   settlement  
0                  поселок  Аксарайский  
1                  поселок      Арсения  
2                     None         None  
3                     None         None  
4          рабочий поселок   Кормиловка  
...                    ...          ...  
67398              деревня      Тимково  
67399              деревня       Батово  
67400      рабочий поселок   Алексеевск  
67401                 None         None  
67402              деревня         Луки  

[67403 rows x 13 columns]

In [23]:
adrs.to_csv('C:/Users/sgulbin/Work/Analysis/FTR_score_v2/v2/data_lib/processed_bp_v2_part4.csv', encoding = 'utf-8-sig', index = False)